# Librairies

In [1]:
import warnings
warnings.filterwarnings("ignore")
import logging
logging.getLogger('cmdstanpy').setLevel(logging.WARNING)

import pandas as pd
from ydata_profiling import ProfileReport # from April, 1st 2023
import datetime
import plotly
import plotly.offline as pyoff
import plotly.graph_objs as go
from plotly.subplots import make_subplots
from prophet import Prophet
from prophet.diagnostics import cross_validation
from prophet.diagnostics import performance_metrics
from prophet.plot import plot_cross_validation_metric
from prophet.serialize import model_to_json, model_from_json

# Analyze traffic dataset ✈

In [2]:
#Import data
traffic_df = pd.read_parquet('traffic_10lines.parquet')

#Data description
traffic_df.describe(include='all').transpose()

count  unique                  top    freq  \
date                  254899    2626  2019-01-02 00:00:00     165   
pax                 254899.0     NaN                  NaN     NaN   
seats               250749.0     NaN                  NaN     NaN   
flight_type           251168      19                    J  240627   
flight_typename       254899       4            Scheduled  251250   
home_airport          254899       8                  LIS  125254   
paired_airport        254899      10                  OPO   72331   
home_airportname      254899       8               Lisbon  125254   
paired_airportname    254899      10                Porto   72331   
distance            254899.0    <NA>                 <NA>    <NA>   
flight_number         251438    2663               TP 433    2332   
airline_iata          248648      90                   TP   91648   
airline_name          254813     131                  TAP   91648   
scheduled_datetime    254899  201668  2019-08-29 18:05:00       5   
direction             254899       2                    D  127622   
home_country          254899       7                   PT  125254   
paired_country        254899       8                   PT   72331   
home_countryname      254899       7             Portugal  125254   
paired_countryname    254899       8             Portugal   72331   
travel_area           254899       4             Domestic  108770   
aircraft_type         251439     168                 A320   30344   

                                  first                 last        mean  \
date                2016-01-01 00:00:00  2023-03-10 00:00:00         NaN   
pax                                 NaN                  NaN  127.082676   
seats                               NaN                  NaN  159.352879   
flight_type                         NaN                  NaN         NaN   
flight_typename                     NaN                  NaN         NaN   
home_airport                        NaN                  NaN         NaN   
paired_airport                      NaN                  NaN         NaN   
home_airportname                    NaN                  NaN         NaN   
paired_airportname                  NaN                  NaN         NaN   
distance                           <NA>                 <NA>  944.365078   
flight_number                       NaN                  NaN         NaN   
airline_iata                        NaN                  NaN         NaN   
airline_name                        NaN                  NaN         NaN   
scheduled_datetime  2016-01-01 06:10:00  2023-03-10 00:50:00         NaN   
direction                           NaN                  NaN         NaN   
home_country                        NaN                  NaN         NaN   
paired_country                      NaN                  NaN         NaN   
home_countryname                    NaN                  NaN         NaN   
paired_countryname                  NaN                  NaN         NaN   
travel_area                         NaN                  NaN         NaN   
aircraft_type                       NaN                  NaN         NaN   

                           std    min    25%     50%     75%      max  
date                       NaN    NaN    NaN     NaN     NaN      NaN  
pax                  53.050019  -11.0   88.0   140.0   168.0    582.0  
seats                47.311964    0.0  144.0   174.0   186.0    615.0  
flight_type                NaN    NaN    NaN     NaN     NaN      NaN  
flight_typename            NaN    NaN    NaN     NaN     NaN      NaN  
home_airport               NaN    NaN    NaN     NaN     NaN      NaN  
paired_airport             NaN    NaN    NaN     NaN     NaN      NaN  
home_airportname           NaN    NaN    NaN     NaN     NaN      NaN  
paired_airportname         NaN    NaN    NaN     NaN     NaN      NaN  
distance            886.540144  277.0  277.0  1109.0  1437.0  11653.0  
flight_number              NaN    NaN  

In [3]:
# Description Report of data using pandas profiling
profile_report = ProfileReport(traffic_df)
profile_report.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [4]:
#Affichage de la date minimum et maximum et du nombre de passager par home airport, paired airport et la direction
(traffic_df
 .groupby(['home_airport', 'paired_airport', 'direction'])
 .agg(date_min=('date', 'min'), date_max=('date', 'max'), pax=('pax', 'sum'))
 .reset_index()
)

home_airport paired_airport direction   date_min   date_max        pax
0           LGW            AMS         A 2016-01-01 2023-03-09  2686346.0
1           LGW            AMS         D 2016-01-01 2023-03-09  2686476.0
2           LGW            BCN         A 2016-01-01 2023-03-10  3813240.0
3           LGW            BCN         D 2016-01-01 2023-03-09  3799836.0
4           LIS            OPO         A 2016-01-01 2023-03-09  2819094.0
5           LIS            OPO         D 2016-01-01 2023-03-09  2813651.0
6           LIS            ORY         A 2016-01-01 2023-03-09  3835664.0
7           LIS            ORY         D 2016-01-01 2023-03-09  3860404.0
8           LYS            PIS         A 2017-11-20 2023-03-09     6173.0
9           LYS            PIS         D 2018-01-02 2023-03-09     4178.0
10          NTE            FUE         A 2019-01-06 2023-03-05    51406.0
11          NTE            FUE         D 2019-01-06 2023-03-05    48448.0
12          PNH            NGB         A 2017-01-11 2020-02-04     5674.0
13          PNH            NGB         D 2016-05-05 2023-03-07     4344.0
14          POP            JFK         A 2018-01-01 2023-03-09   244235.0
15          POP            JFK         D 2018-01-01 2023-03-09   248199.0
16          SCL            LHR         A 2019-01-01 2023-03-07    95959.0
17          SCL            LHR         D 2019-01-01 2023-03-07    97734.0
18          SSA            GRU         A 2019-01-01 2023-03-09  2609960.0
19          SSA            GRU         D 2019-01-01 2023-03-09  2662226.0

In [5]:
#Liste home airport dans la base de données
list_home_air = list(traffic_df['home_airport'].value_counts().index)
print(list_home_air)

#Liste paired airport dans la base de donnée
list_paired_air = list(traffic_df['paired_airport'].value_counts().index)
print(list_paired_air)

['LIS', 'LGW', 'SSA', 'POP', 'SCL', 'NTE', 'LYS', 'PNH']
['OPO', 'ORY', 'BCN', 'AMS', 'GRU', 'JFK', 'LHR', 'FUE', 'PIS', 'NGB']


# Data visualisation

In [6]:
def draw_ts_multiple(df: pd.DataFrame, v1: str, v2: str=None, prediction: str=None, date: str='date',
              secondary_y=True, covid_zone=False, display=True):
    """
    Draw times series possibly on two y axis.
    Args:
    - df (pd.DataFrame): time series dataframe (one line per date, series in columns)
    - v1 (str | list[str]): name or list of names of the series to plot on the first x axis
    - v2 (str): name of the serie to plot on the second y axis (default: None)
    - prediction (str): name of v1 hat (prediction) displayed with a dotted line (default: None)
    - date (str): name of date column for time (default: 'date')
    - secondary_y (bool): use a secondary y axis if v2 is used (default: True)
    - covid_zone (bool): highlight COVID-19 period with a grayed rectangle (default: False)
    - display (bool): display figure otherwise just return the figure (default: True)

    Returns:
    - fig (plotly.graph_objs._figure.Figure): Plotly figure generated

    Notes:
    Make sure to use the semi-colon trick if you don't want to have the figure displayed twice.
    Or use `display=False`.
    """
    if isinstance(v1, str):
        variables = [(v1, 'V1')]
    else:
        variables = [(v, 'V1.{}'.format(i)) for i, v in enumerate(v1)]
    title = '<br>'.join([n + ': '+ v for v, n in variables]) + ('<br>V2: ' + v2) if v2 else '<br>'.join([v + ': '+ n for v, n in variables])
    layout = dict(
    title=title,
    xaxis=dict(
        rangeselector=dict(
            buttons=list([
                dict(count=1,
                     label='1m',
                     step='month',
                     stepmode='backward'),
                dict(count=6,
                     label='6m',
                     step='month',
                     stepmode='backward'),
                dict(step='all')
            ])
        ),
        rangeslider=dict(
            visible = True
        ),
        type='date'
    )
  )
    fig = make_subplots(specs=[[{"secondary_y": True}]])
    fig.update_layout(layout)
    for v, name in variables:
        fig.add_trace(go.Scatter(x=df[date], y=df[v], name=name), secondary_y=False)
        if v2:
            fig.add_trace(go.Scatter(x=df[date], y=df[v2], name='V2'), secondary_y=secondary_y)
            fig['layout']['yaxis2']['showgrid'] = False
            fig.update_yaxes(rangemode='tozero')
            fig.update_layout(margin=dict(t=125 + 30 * (len(variables) - 1)))
        if prediction:
            fig.add_trace(go.Scatter(x=df[date], y=df[prediction], name='^V1', line={'dash': 'dot'}), secondary_y=False)

        if covid_zone:
            fig.add_vrect(
                x0=pd.Timestamp("2020-03-01"), x1=pd.Timestamp("2022-01-01"),
                fillcolor="Gray", opacity=0.5,
                layer="below", line_width=0,
            )
        if display:
            pyoff.iplot(fig)
    return fig

In [7]:
#Define a function to display a trafic graph
def air_flux(home_airport : str, paired_airport: str):
    
    """
    Display a number of passenger per date
    
    Parameters:
    - homeAirport (str): IATA Code for home airport
    - pairedAirport (str): IATA Code for paired airport

    Returns:
    - Ploly Graph: aggregated daily PAX traffic on route (home-paired)
    """
    
    draw_ts_multiple(
        (traffic_df
         .query('home_airport == "{}" and paired_airport == "{}"'.format(home_airport, paired_airport))
         .groupby(['home_airport', 'paired_airport', 'date'])
         .agg(pax_total=('pax', 'sum'))
         .reset_index()
        ),
        'pax_total',
        covid_zone=True,
    )

In [8]:
#display for home_airport = "LGW" , paired_airport = "AMS"
air_flux(home_airport = "LGW" , paired_airport = "AMS" )

In [9]:
#display for home_airport = 'SSA' , paired_airport = 'GRU'
air_flux(home_airport = 'SSA' , paired_airport = 'GRU' )

# Model prediction

In [10]:
def generate_route_df(traffic_df: pd.DataFrame, homeAirport: str, pairedAirport: str) -> pd.DataFrame:
    
    """
    Extract route dataframe from traffic dataframe for route from home airport to paired airport

    Args:
    - traffic_df (pd.DataFrame): traffic dataframe
    - homeAirport (str): IATA Code for home airport
    - pairedAirport (str): IATA Code for paired airport

    Returns:
    - pd.DataFrame: aggregated daily PAX traffic on route (home-paired)
    """
    _df = (traffic_df
         .query('home_airport == "{home}" and paired_airport == "{paired}"'.format(home=homeAirport, paired=pairedAirport))
         .groupby(['home_airport', 'paired_airport', 'date'])
         .agg(pax_total=('pax', 'sum'))
         .reset_index()
         )
    return _df

In [11]:
#Generate data for home_airport = "LGW" , paired_airport = "AMS"
data = generate_route_df(traffic_df, "LGW", "AMS").rename(columns={'date': 'ds', 'pax_total': 'y'})
data

home_airport paired_airport         ds       y
0             LGW            AMS 2016-01-01  3081.0
1             LGW            AMS 2016-01-02  2334.0
2             LGW            AMS 2016-01-03  3341.0
3             LGW            AMS 2016-01-04  2665.0
4             LGW            AMS 2016-01-05  1996.0
...           ...            ...        ...     ...
2243          LGW            AMS 2023-03-05  2815.0
2244          LGW            AMS 2023-03-06  1916.0
2245          LGW            AMS 2023-03-07  1741.0
2246          LGW            AMS 2023-03-08  1432.0
2247          LGW            AMS 2023-03-09  2029.0

[2248 rows x 4 columns]

## Prophet model for prediction

In [12]:
# Fit the model
baseline_model = Prophet()
baseline_model.fit(data)

15:38:38 - cmdstanpy - INFO - Chain [1] start processing
15:38:38 - cmdstanpy - INFO - Chain [1] done processing


In [13]:
# Prepare to predict 15 days
future_df = baseline_model.make_future_dataframe(periods=100) 
future_df

ds
0    2016-01-01
1    2016-01-02
2    2016-01-03
3    2016-01-04
4    2016-01-05
...         ...
2343 2023-06-13
2344 2023-06-14
2345 2023-06-15
2346 2023-06-16
2347 2023-06-17

[2348 rows x 1 columns]

In [14]:
#Forecost the 15 days
forecast = baseline_model.predict(future_df)
df_forecast = forecast[['ds', 'yhat', 'yhat_lower', 'yhat_upper']]
df_forecast.head()

ds         yhat   yhat_lower   yhat_upper
0 2016-01-01  3345.827047  2870.895050  3848.816570
1 2016-01-02  2105.576313  1643.862599  2571.991225
2 2016-01-03  2974.842051  2480.333957  3463.299145
3 2016-01-04  3025.816293  2561.049512  3556.482452
4 2016-01-05  2446.133894  1919.547230  2937.258335

In [15]:
#Plot 

trace_open = go.Scatter(
    x = df_forecast["ds"],
    y = df_forecast["yhat"],
    mode = 'lines',
    line = {"color": "green"},
    name="Forecast"
)

trace_close = go.Scatter(
    x = data["ds"],
    y = data["y"],
    mode ="lines",
    line = {"color": "blue"},
    name="Data values"
)


In [16]:
data_for = [trace_open, trace_close]

layout = go.Layout(title="Passenger Flux Forecast",xaxis_rangeslider_visible=True)

fig = go.Figure(data=data_for,layout=layout)

plotly.offline.iplot(fig)

### Performance evaluation

In [17]:
eval_df = cross_validation(baseline_model, initial='366 days', period='90 days', horizon='90 days')
eval_df

  0%|          | 0/25 [00:00<?, ?it/s]

15:38:40 - cmdstanpy - INFO - Chain [1] start processing
15:38:40 - cmdstanpy - INFO - Chain [1] done processing
15:38:40 - cmdstanpy - INFO - Chain [1] start processing
15:38:40 - cmdstanpy - INFO - Chain [1] done processing
15:38:40 - cmdstanpy - INFO - Chain [1] start processing
15:38:40 - cmdstanpy - INFO - Chain [1] done processing
15:38:40 - cmdstanpy - INFO - Chain [1] start processing
15:38:40 - cmdstanpy - INFO - Chain [1] done processing
15:38:41 - cmdstanpy - INFO - Chain [1] start processing
15:38:41 - cmdstanpy - INFO - Chain [1] done processing
15:38:41 - cmdstanpy - INFO - Chain [1] start processing
15:38:41 - cmdstanpy - INFO - Chain [1] done processing
15:38:41 - cmdstanpy - INFO - Chain [1] start processing
15:38:41 - cmdstanpy - INFO - Chain [1] done processing
15:38:42 - cmdstanpy - INFO - Chain [1] start processing
15:38:42 - cmdstanpy - INFO - Chain [1] done processing
15:38:42 - cmdstanpy - INFO - Chain [1] start processing
15:38:42 - cmdstanpy - INFO - Chain [1]

ds         yhat   yhat_lower   yhat_upper       y     cutoff
0    2017-01-10  2369.327490  1985.346698  2717.109459  1964.0 2017-01-09
1    2017-01-11  2456.679674  2122.297949  2789.064804  1946.0 2017-01-09
2    2017-01-12  2830.251159  2477.282424  3173.848088  2495.0 2017-01-09
3    2017-01-13  3362.344196  3003.014407  3699.426989  3482.0 2017-01-09
4    2017-01-14  1905.820758  1556.547408  2251.304714  2065.0 2017-01-09
...         ...          ...          ...          ...     ...        ...
1868 2023-03-05  3238.662645  2757.044162  3729.582629  2815.0 2022-12-09
1869 2023-03-06  3312.080639  2842.674892  3803.262986  1916.0 2022-12-09
1870 2023-03-07  2739.181574  2259.198620  3210.607651  1741.0 2022-12-09
1871 2023-03-08  2790.741666  2336.586406  3231.100541  1432.0 2022-12-09
1872 2023-03-09  3222.810797  2740.825010  3699.729677  2029.0 2022-12-09

[1873 rows x 6 columns]

In [18]:
#Performance Metrics
performance_metrics(eval_df)

horizon           mse         rmse         mae     mdape     smape  \
0   9 days  5.387225e+05   733.977209  501.661115  0.129789  0.487594   
1  10 days  5.489990e+05   740.944659  494.249724  0.128329  0.474756   
2  11 days  5.869954e+05   766.156262  505.318378  0.123139  0.479837   
3  12 days  5.608235e+05   748.881480  505.071404  0.118352  0.486272   
4  13 days  5.984944e+05   773.624167  505.304485  0.110595  0.478083   
..     ...           ...          ...         ...       ...       ...   
77 86 days  1.329802e+06  1153.170311  789.464230  0.143125  0.600956   
78 87 days  1.397879e+06  1182.319125  811.625373  0.141006  0.607388   
79 88 days  1.409237e+06  1187.113071  817.830151  0.138167  0.608669   
80 89 days  1.387772e+06  1178.037495  811.221851  0.138167  0.606177   
81 90 days  1.395966e+06  1181.510194  812.742407  0.131087  0.616477   

    coverage  
0   0.593583  
1   0.617520  
2   0.634176  
3   0.634581  
4   0.636364  
..       ...  
77  0.505348  
78  0.508021  
79  0.508021  
80  0.514133  
81  0.526865  

[82 rows x 7 columns]

In [19]:
#Plot of metrics performance
plot_cross_validation_metric(eval_df, metric='rmse');

### Automate model fitting and evaluation

In [20]:
routes = (traffic_df
 .drop_duplicates(subset=['home_airport', 'paired_airport'])
 [['home_airport', 'paired_airport']]
 .to_dict(orient='rows')
)

In [21]:
routes

[{'home_airport': 'LGW', 'paired_airport': 'BCN'},
 {'home_airport': 'LGW', 'paired_airport': 'AMS'},
 {'home_airport': 'LIS', 'paired_airport': 'ORY'},
 {'home_airport': 'LIS', 'paired_airport': 'OPO'},
 {'home_airport': 'SSA', 'paired_airport': 'GRU'},
 {'home_airport': 'NTE', 'paired_airport': 'FUE'},
 {'home_airport': 'LYS', 'paired_airport': 'PIS'},
 {'home_airport': 'PNH', 'paired_airport': 'NGB'},
 {'home_airport': 'POP', 'paired_airport': 'JFK'},
 {'home_airport': 'SCL', 'paired_airport': 'LHR'}]

In [22]:
models = dict()
performances = dict()

for route in routes:
    print(route)
    home = route['home_airport']
    paired = route['paired_airport']
    # Build route traffic dataframe
    _df = generate_route_df(traffic_df, home, paired)
    # Create a model
    _model = Prophet()
    # Fit the model
    _model.fit(_df.rename(columns={'date': 'ds', 'pax_total': 'y'}))
    # Cross validate the model
    _cv_df = cross_validation(_model, horizon='90 days', parallel="processes")
    _perf_df = performance_metrics(_cv_df, rolling_window=1)
     # Save results
    models[(route['home_airport'], route['paired_airport'])] = _model
    performances[(route['home_airport'], route['paired_airport'])] = _perf_df['rmse'].values[0]

{'home_airport': 'LGW', 'paired_airport': 'BCN'}


15:38:51 - cmdstanpy - INFO - Chain [1] start processing
15:38:51 - cmdstanpy - INFO - Chain [1] done processing


{'home_airport': 'LGW', 'paired_airport': 'AMS'}


15:39:16 - cmdstanpy - INFO - Chain [1] start processing
15:39:17 - cmdstanpy - INFO - Chain [1] done processing


{'home_airport': 'LIS', 'paired_airport': 'ORY'}


...

15:41:39 - cmdstanpy - INFO - Chain [1] start processing
15:41:40 - cmdstanpy - INFO - Chain [1] done processing


{'home_airport': 'POP', 'paired_airport': 'JFK'}


15:41:49 - cmdstanpy - INFO - Chain [1] start processing
15:41:50 - cmdstanpy - INFO - Chain [1] done processing


{'home_airport': 'SCL', 'paired_airport': 'LHR'}


15:42:06 - cmdstanpy - INFO - Chain [1] start processing
15:42:06 - cmdstanpy - INFO - Chain [1] done processing


In [23]:
models

{('LGW', 'BCN'): <prophet.forecaster.Prophet at 0x19f02533fa0>,
 ('LGW', 'AMS'): <prophet.forecaster.Prophet at 0x19f03348a00>,
 ('LIS', 'ORY'): <prophet.forecaster.Prophet at 0x19f045efb20>,
 ('LIS', 'OPO'): <prophet.forecaster.Prophet at 0x19f6fead780>,
 ('SSA', 'GRU'): <prophet.forecaster.Prophet at 0x19f04a918d0>,
 ('NTE', 'FUE'): <prophet.forecaster.Prophet at 0x19f04bbfd30>,
 ('LYS', 'PIS'): <prophet.forecaster.Prophet at 0x19f6feaf460>,
 ('PNH', 'NGB'): <prophet.forecaster.Prophet at 0x19f6feae860>,
 ('POP', 'JFK'): <prophet.forecaster.Prophet at 0x19f6feae050>,
 ('SCL', 'LHR'): <prophet.forecaster.Prophet at 0x19f04a93a90>}

In [24]:
performances

{('LGW', 'BCN'): 1253.154090155653,
 ('LGW', 'AMS'): 925.8531954294384,
 ('LIS', 'ORY'): 870.2145779842895,
 ('LIS', 'OPO'): 610.4933181999372,
 ('SSA', 'GRU'): 1947.6507663624789,
 ('NTE', 'FUE'): 192.46096090441867,
 ('LYS', 'PIS'): 624.9991134736619,
 ('PNH', 'NGB'): 1559.215830465532,
 ('POP', 'JFK'): 76.79121042726484,
 ('SCL', 'LHR'): 146.97993496014755}

### Save models

In [26]:
for model in models:
    _filename = 'models/route_model_prophet_{home}_{paired}.json'.format(home=model[0], paired=model[1])
    with open(_filename, 'w') as f:
        f.write(model_to_json(models[model]))